# Generate hole region files

## I. Produce simple 10 arcsec holes. 
First we produce the simplest possible hole regions. For every star brighter than 16 Mag it puts a 10 arcsec circle. 

We then go on to produce varying size holes for individual pristine catalogues based on parameters computed by Seb Oliver's IDL code.

In [1]:
from herschelhelp_internal import git_version
print("This notebook was run with herschelhelp_internal version: \n{}".format(git_version()))

This notebook was run with herschelhelp_internal version: 
33f5ec7 (Wed Dec 6 16:56:17 2017 +0000) [with local modifications]


In [2]:
from herschelhelp_internal import starmask
from pymoc import MOC

import time
import os

In [3]:
OUT_DIR = os.environ.get('OUT_DIR', "./data")
SUFFIX = os.environ.get('SUFFIX', time.strftime("%Y%m%d"))
SUFFIX = SUFFIX #+ '_v2'

try:
    os.makedirs(OUT_DIR)
except FileExistsError:
    pass

field = 'Lockman-SWIRE'

First we list all the fields including the ra and dec of the first star in the field. We do this because, due to a peculiarity of the pyregion code, we must supply an image header to produce mocs.

In [4]:
#Field names plus ra dec of first circle
fields= {
# Field                RA              DEC
'AKARI-NEP':          [274.654402036,  65.7962520276 ],
'AKARI-SEP':          [72.2316923316, -54.380443672  ],
'Bootes':             [216.431700722,  32.401081899  ],
'CDFS-SWIRE':         [51.0227099923, -29.8185285737 ],
'COSMOS':             [149.295925951,  1.08212668291 ],
'EGS':                [217.276981956,  53.6441519854 ],
'ELAIS-N1':           [247.096600963,  55.1757687739 ],
'ELAIS-N2':           [248.424493154,  39.1274077489 ],
'ELAIS-S1':           [7.10625839472, -43.8632559768 ],
'GAMA-09':            [129.076050945, -2.23171513025 ],
'GAMA-12':            [172.84437099,  -0.482115877707],
'GAMA-15':            [211.756497623, -2.28573712848 ],
'HDF-N':              [190.259734752,  62.205265532  ],
'Herschel-Stripe-82': [353.751913281, -7.10891111165 ],
'Lockman-SWIRE':      [161.942787703,  59.0563805825 ],
'NGP':                [192.899559129,  22.0990890388 ],
'SA13':               [197.895801254,  42.4400105492 ],
'SGP':                [334.297748942, -34.5037863499 ],
'SPIRE-NEP':          [266.334305546,  68.7904496043 ],
'SSDF':               [341.577544902, -59.1868365369 ],
'xFLS':               [261.387059958,  58.0184602211 ],
'XMM-13hr':           [203.318355937,  37.4745777866 ],
'XMM-LSS':            [32.9413834032, -6.02293494708 ]}



Then we generate a region file to define all the holes. At present this is very crude and simply puts a 10 arcsec hole over every star brighter than 16 Mag.

In [5]:
starmask.create_holes('../../dmu0/dmu0_GAIA/data/GAIA_{}.fits'.format(field),
                      'data/10_arcsec_holes_{}.reg'.format(field),
                      '../../dmu2/dmu2_field_coverages/{}_MOC.fits'.format(field))
    


There are 58813 GAIA stars in Lockman-SWIRE
Starmask written to data/10_arcsec_holes_Lockman-SWIRE.reg


Then we convert the region files to MOC format. We recomend against using the MOC since, even at this high order, it doesn't capture shape that well. This will become increasingly significant if we have smaller or more detailed shapes in the future.

In [6]:
ORDER=16
starmask.reg2moc('data/10_arcsec_holes_{}.reg'.format(field),
            '../../dmu2/dmu2_field_coverages/{}_MOC.fits'.format(field),
            'data/10_arcsec_holes_{}_O'.format(field) + str(ORDER) + '_MOC.fits',
            ra_typ=fields[field][0],
            dec_typ=fields[field][1],
            order=ORDER)


WCSAXES =                    2 / Number of coordinate axes
CRPIX1  =            [astropy.io.fits.card]
     0.5 / Pixel coordinate of reference point
CRPIX2  =                0.5 / Pi [astropy.io.fits.card]
xel coordinate of reference point
CDELT1  =                0.675 / [deg] Coordin [astropy.io.fits.card]
ate increment at reference point
CDELT2  =                0.675 / [deg] Coordina [astropy.io.fits.card]
te increment at reference point
RADECSYSa= 'ICRS    '           / International  [astropy.io.fits.card]
Celestial Ref. System
CUNIT1  = 'deg     '                / Units of coordinate  [astropy.io.fits.card]
increment and value
CUNIT2  = 'deg     '                / Units of coordinate in [astropy.io.fits.card]
crement and value
CTYPE1  = 'RA---TAN'           / 
CTYPE2  = 'DEC--TAN'         [astropy.io.fits.card]
   / 
CRVAL1  =                  161.942787703 / [deg] Coordinate value at refer [astropy.io.fits.card]
ence point
CRVAL2  =                  59.0563805825 / [deg] Coor

## II Produce magnitude varying holes
Then we produce a varying hole parameterised by Seb's code. We define an annulus with a 1 arcsec circle at the centre and an outer radius r_50 (the radius at which the artefact density goes over 0.5 x background density) = 10^(A + B x mag).

In [7]:
# Run Lockman-SWIRE with parameters from IDL code. The IDL output files are in ./data/

per_catalogue_params = [
#     Field       Band        A         B            magnitude limit
    [field, 'megacam_r',      2.30374,  -0.0962746,  18], # Using 18 as faint limit.
    [field, 'gpc1_r',         2.46029,  -0.111433,   18], # Using 18 as faint limit. 
    [field, 'irac1',          2.56501,  -0.100879,   18], # Using 18 as faint limit.
    [field, 'ukidss_k',       3.67944,  -0.173850,   18], # Using 18 as faint limit.
    [field, 'wfc_r',          3.43951,  -0.173789,   18]  # Using 18 as faint limit.
]   

#We previously took a moc of the survey to only make holes on that area, which 
#was a mistake as it led to missing holes for the XID+ run

#Combine SERVS and SWIRE mocs because irac1 fluxes can be from either
#swire_moc = MOC(filename = '../../dmu0/dmu0_DataFusion-Spitzer/data/DF-SWIRE_{}_MOC.fits'.format(field))
#servs_moc = MOC(filename = '../../dmu0/dmu0_DataFusion-Spitzer/data/DF-SERVS_{}_MOC.fits'.format(field))
#irac1_moc = swire_moc + servs_moc
#irac1_moc.write('data/SERVS_SWIRE_COVERAGE_irac1_{}_MOC.fits'.format(field), filetype='fits' ,overwrite=True)

#moc_files = {
#    'megacam_r'  :'data/SERVS_SWIRE_COVERAGE_irac1_{}_MOC.fits'.format(field),
#    'gpc1_r' :'../../dmu0/dmu0_PanSTARRS1-3SS/data/PanSTARRS1-3SS_{}_MOC.fits'.format(field),
#    'irac1'  :'data/SERVS_SWIRE_COVERAGE_irac1_{}_MOC.fits'.format(field),
#    'ukidss_k':'../../dmu0/dmu0_UKIDSS-DXS/data/UKIDSS-DXS_{}_MOC.fits'.format(field),
#    'wfc_r':'../../dmu0/dmu0_INTWFC/data/lh_intwfc_v2.1_HELP_coverage_MOC.fits'
#}

In [8]:
for pristine_cat in per_catalogue_params:
    starmask.create_holes('../../dmu0/dmu0_GAIA/data/GAIA_{}.fits'.format(pristine_cat[0]),    #GAIA catalogue
                          'data/holes_{}_{}_{}.reg'.format(field,pristine_cat[1],SUFFIX), #output file
                          '../../dmu2/dmu2_field_coverages/{}_MOC.fits'.format(field),                                       #moc of survey region
                          AB = [pristine_cat[2],pristine_cat[3]],                           #radius as f of mag params
                          mag_lim = pristine_cat[4])                                        #upper magnitude limit

There are 58813 GAIA stars in Lockman-SWIRE
Starmask written to data/holes_Lockman-SWIRE_megacam_r_20171214.reg
There are 58813 GAIA stars in Lockman-SWIRE
Starmask written to data/holes_Lockman-SWIRE_gpc1_r_20171214.reg
There are 58813 GAIA stars in Lockman-SWIRE
Starmask written to data/holes_Lockman-SWIRE_irac1_20171214.reg
There are 58813 GAIA stars in Lockman-SWIRE
Starmask written to data/holes_Lockman-SWIRE_ukidss_k_20171214.reg
There are 58813 GAIA stars in Lockman-SWIRE
Starmask written to data/holes_Lockman-SWIRE_wfc_r_20171214.reg


Again we convert the region files to MOC format.

In [9]:
ORDER=16
for pristine_cat in per_catalogue_params:
    starmask.reg2moc('data/holes_{}_{}_{}.reg'.format(field,pristine_cat[1],SUFFIX),
            '../../dmu2/dmu2_field_coverages/{}_MOC.fits'.format(field),
            'data/holes_{}_{}_{}_O{}_MOC.fits'.format(field,pristine_cat[1],SUFFIX,str(ORDER)),
            ra_typ=fields[field][0],
            dec_typ=fields[field][1],
            order=ORDER)


WCSAXES =                    2 / Number of coordinate axes
CRPIX1  =            [astropy.io.fits.card]
     0.5 / Pixel coordinate of reference point
CRPIX2  =                0.5 / Pi [astropy.io.fits.card]
xel coordinate of reference point
CDELT1  =                0.675 / [deg] Coordin [astropy.io.fits.card]
ate increment at reference point
CDELT2  =                0.675 / [deg] Coordina [astropy.io.fits.card]
te increment at reference point
RADECSYSa= 'ICRS    '           / International  [astropy.io.fits.card]
Celestial Ref. System
CUNIT1  = 'deg     '                / Units of coordinate  [astropy.io.fits.card]
increment and value
CUNIT2  = 'deg     '                / Units of coordinate in [astropy.io.fits.card]
crement and value
CTYPE1  = 'RA---TAN'           / 
CTYPE2  = 'DEC--TAN'         [astropy.io.fits.card]
   / 
CRVAL1  =                  161.942787703 / [deg] Coordinate value at refer [astropy.io.fits.card]
ence point
CRVAL2  =                  59.0563805825 / [deg] Coor